# Analyse des ventes
---
<div class="alert alert-block alert-info">
<b>🗣</b>Ce projet est un exemple dont le but est de vous aidez à envisager les problèmes liés à votre entreprise sous l'angle de l'analyse de vos données. Notre objectif  est de vous démontrer que l'extraction de connaissances à partir de vos données facilite les prises de décisions et constitue un avantage stratégique.
</div>

## Sommaire
Dans cet exemple __nous analyserons les ventes d'une entreprise fictif en ligne d’électronique localisé au US__
1. [Présentation des données](#load)
2. [meilleurs ventes](#cleanning)
3. [meilleur moment pour la pub](#augment)

In [180]:
import os
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

np.random.seed(42)

import plotly.io as pio
pio.renderers.default = "notebook"
pio.templates.default = "plotly_white"

### usefull function

In [181]:
# Readable big number
def millify(n):
    if n>999:
        if n > 1e6-1:
            return f'{round(n/1e6,1)}M'
        return f'{round(n/1e3,1)}K'
    return n

In [182]:
# get acess to mapbox
with open('mapbox_token.txt') as f:
    lines=[x.rstrip() for x in f]
    
mapbox_access_token = lines[0]
px.set_mapbox_access_token(mapbox_access_token)

In [183]:
# color per categories
colors_palette = {'Computers':'#264653',
           'Phone':'#2a9d8f',
           'Gears':'#e9c46a',
           'TV & Monitor':'#f4a261',
           'Washing Machine':'#e76f51'}
str_to_int = {key: i for i, key in enumerate(colors_palette.keys())}

## 1. Présentation des données 
---
__Les données utilisées représente les ventes réalisé par une entreprise d'électronique lors de l’année 2019__.  On y retrouve des informations pertinentes sur nos clients, tel que les `produits achetés` par ce dernier, `l'heure d'achat` où encore `l’adresse de livraison`. Voici-ci dessous un descriptif des données collecter.

In [184]:
pd.read_csv('all_data.csv').head()

Order ID               Product Quantity Ordered Price Each      Order Date  \
0   295665    Macbook Pro Laptop                1       1700  12/30/19 00:01   
1   295666    LG Washing Machine                1      600.0  12/29/19 07:03   
2   295667  USB-C Charging Cable                1      11.95  12/12/19 18:21   
3   295668      27in FHD Monitor                1     149.99  12/22/19 15:13   
4   295669  USB-C Charging Cable                1      11.95  12/18/19 12:38   

                         Purchase Address  
0  136 Church St, New York City, NY 10001  
1     562 2nd St, New York City, NY 10001  
2    277 Main St, New York City, NY 10001  
3     410 6th St, San Francisco, CA 94016  
4           43 Hill St, Atlanta, GA 30301

↳ Le client répertorié par l'id __295665__ a acheté un __Macbook Pro__  à __1700$__ le __30 décembre 2019 à 00:01__, son adress de livraison est __136 Church St, New York City, NY 10001__ 

### Descriptif des données collectées
- __ID__, numéro unique par client 
- __Produit__, nom du matériel informatique acheté 
- __Quantité commandée__, nombre d’exemplaires vendu
- __Prix__, prix unnitaire de chaque produit
- __Date__, date et heure de l'achat
- __Adresse__, adresse de livraison
- __Catégorie__, nature du produit (Computers, Washing Machine, Gears, TV & Monitor, Phone)

In [185]:
# skip all the cleanning and data preparation 
data = pd.read_csv('clean_data.csv')

### Première analyse

In [186]:
city_dropdown = 'San Francisco'
city_dropdown = None

if city_dropdown:
    df = data[data['City'] == city_dropdown]
else:
    df = data.copy()

In [187]:
total_sales = np.round(df['Sales'].sum())
total_orders = len(df.groupby(['Order ID', 'Order Date']).count())
mean_per_sales = int(total_sales/total_orders)
print('{} $ de ventes pour un total de {} commandes'.format(millify(total_sales),total_orders))
print(' ↳ soit une moyenne de {} $ par commande'.format(mean_per_sales))
# np.round(data['Sales'].mean())

34.5M $ de ventes pour un total de 178437 commandes
 ↳ soit une moyenne de 193 $ par commande


Durant l’année 2019, l'entreprise d'électronique à réaliser __34,5 Millions de dollars de ventes pour 209 079 commandes__. En moyenne chaque vente correspond à une vente de 193 $ 

## 2. Présentation des produits 
---
Notre entreprise d’électronique vend __19 produits__ différents regroupés en __5 catégories__. On constate par exemple que seulement deux type d’ordinateur sont vendus, le macbook pro et le ThinkPad Laptop. Explorer par vous même la gamme des produits vendu par cette entreprise d'électronique.

In [376]:
# data
df = data.groupby(['Categories', 'Product']).sum()
df = df.reset_index().sort_values('Categories')
# create dimensions
cat_dim = go.parcats.Dimension(values=df['Categories'].values, label='Categorie')
product_dim = go.parcats.Dimension(values=df['Product'].values, label='Produit')
# color 
colors = df['Categories'].apply(lambda x:str_to_int[x])
colorscale = [value for value in colors_palette.values()]
# plot
fig = go.Figure(go.Parcats(
    dimensions=[cat_dim, product_dim],
    line={'color': colors, 'colorscale': colorscale, 'shape': 'hspline'},
    labelfont = dict(size = 15),
    hoverinfo='none'))

fig.show()

Maintenant que nous connaissons un peu mieux les produits vendus focalisont nous sur nos ventes

### Quel produit se vend le mieux ?

In [505]:
# filters in dash
dropdown_type = 'Sales' 
dropdown_type = 'Quantity Ordered'

In [506]:
# Product Bar Chart
best_product = data.groupby(['Categories','Product']).sum()[dropdown_type]
best_product = best_product.sort_values().reset_index()
best_product = best_product.set_index('Product')

# plot
fig= go.Figure()
legend_list = []
for product in best_product.index:
    cat = best_product.loc[product,'Categories']
    if cat in legend_list:
        legend_status = False
    else:
        legend_status = True
        legend_list.append(cat)        
    
    fig.add_trace(go.Bar(
    y = [product], 
    x = [best_product.loc[product,dropdown_type]],
    marker_color = colors_palette[cat],
    orientation='h',
    legendgroup=cat,
    showlegend=legend_status,
    name=cat))

# updates
fig.update_layout(hovermode = 'y unified', 
                  height=700, title = 'Quels sont les produits qui se sont le mieux vendus en 2019?',
                  hoverlabel=dict(bgcolor="white",font_size=12),
                 legend=dict(
                     orientation="h",
                     yanchor="bottom", y=1,
                     xanchor="right", x=0.95))
fig.update_yaxes(showgrid=False)
if dropdown_type == 'Sales':
    fig.update_xaxes(title='Montant des ventes ($)')
    fig.update_traces(hovertemplate='%{x} $ de ventes<extra></extra>')
else:
    fig.update_xaxes(title='Quantité de ventes')
    fig.update_traces(hovertemplate='%{x} commandes<extra></extra>')
    
fig.show()

### Volume de ventes par categories et par produit
↳ pie interactif selon les catégories 

In [507]:
# best_product.reset_index(inplace=True)
# categories
cat = data.groupby('Categories').sum()[dropdown_type].reset_index()
cat['parents'] = '' 
cat['colors'] = cat['Categories'].apply(lambda x: colors_palette[x]) 
cat = cat.rename(columns={'Categories':'labels'})
cat['percents'] = np.round(cat[dropdown_type] / cat[dropdown_type].sum() * 100,1)
# product
# product = best_product[['Product',dropdown_type,'Categories']]
product = data.groupby(['Categories','Product']).sum()[dropdown_type].reset_index()
product = product.rename(columns={'Categories':'parents', 'Product':'labels'})
product['percents'] = np.round(product[dropdown_type] / product[dropdown_type].sum() * 100,1)

df = pd.concat([cat,product])
df['hover_data'] = df[dropdown_type].map(lambda x: millify(x))

# plot
fig =go.Figure(go.Sunburst(
    labels= df['labels'],
    parents=df['parents'],
    values=df[dropdown_type],
    branchvalues='total',
    marker=dict(colors=df['colors']),
    customdata=df['percents'],
    maxdepth=2))
fig.update_layout(margin = dict(t=0, l=0, r=0, b=0))

if dropdown_type == 'Sales':
    fig.update_traces( hovertemplate='<b>%{label}</b><br>'+
    '%{value:.2s} $ de ventes<br>'+'↳ %{customdata}% du total des ventes<extra></extra>')
else:
        fig.update_traces( hovertemplate='<b>%{label}</b><br>'+
    '%{value:.2s} commandes<br>'+'↳ %{customdata}% du nombre total de commandes<extra></extra>')

fig.show()

In [508]:
# data
df = data.groupby(['Categories', 'Product']).sum()[dropdown_type]
df = df.sort_values(ascending=False).reset_index()
# create dimensions
cat_dim = go.parcats.Dimension(values=df['Categories'].values,label='Categorie')
product_dim = go.parcats.Dimension(values=df['Product'].values, label='Produit')
# color 
colors = df['Categories'].map(lambda x: colors_palette[x])

# plot
fig = go.Figure(go.Parcats(
    dimensions=[cat_dim, product_dim],
    line={'color': colors, 'colorscale': colorscale, 'shape': 'hspline'},
    counts=df[dropdown_type],
    labelfont={'size': 16}))

if dropdown_type == 'Sales':
    fig.update_traces(hovertemplate='<b>%{category}</b><br>'+'%{count:.3s} $ de ventes<br>'
                      +'↳ %{probability:.1%} des ventes en 2019<br>')
else:
        fig.update_traces( hovertemplate='<b>%{category}</b><br>'+'%{count:.3s} commandes<br>'
                      +'↳ %{probability:.1%} des commandes en 2019<br>')
fig.update_layout(hovermode='y unified')
fig.show()

## 3. Présentation des lieux de ventes
---
Le service de livraison est disponible dans 9 villes Américaine 

In [391]:
df = data[['lat','long', 'City']].drop_duplicates()
cities = df['City']
fig = go.Figure(go.Scattermapbox(
        lat = df['lat'], 
        lon = df['long'],
        marker = dict(size=10),
        opacity = 0.9,
        hovertemplate ='<b>%{text}</b><br><extra></extra>',
        mode="markers+text",
        text = cities,
        textposition="top center",
    textfont=dict(
        family="sans serif",
        size=16,
        )))
                     
fig.update_layout(hoverlabel=dict(bgcolor="white",font_size=12),
                       width=800, 
                       height=600,
                       mapbox = dict(accesstoken = mapbox_access_token,
                                     zoom = 2.9,
                                     center = go.layout.mapbox.Center(lat=42,lon=-97),
                                    ), 
                       showlegend=False)
fig.show()

💬 supprimer la possibilité de zoomer avec dash

### Quelle est la ville qui a réalisé le plus grand nombre de ventes ?

bof jamais j'aurais dit que dallas est plus gros que atlanta ! Jolie mais pas forcement très parlant quand les valeurs sont proche entre elles!

In [497]:
categories = data.groupby('Categories').sum()[dropdown_type].sort_values(ascending=False).index
city_sales = data.groupby(['City','Categories']).sum()[dropdown_type]
city_sales = city_sales.reset_index(level=0)
# create the % of sales per city
city_sales[dropdown_type]/city_sales.groupby('City').sum()[dropdown_type]
sales_per_city = city_sales.groupby('City').sum()[dropdown_type]
sales_per_city.rename('total_per_city', inplace=True)
city_sales = pd.merge(city_sales,sales_per_city,left_on='City',right_index=True)
city_sales['percents'] = np.round(city_sales[dropdown_type]/city_sales['total_per_city'] * 100)

In [502]:
# plot
fig= go.Figure([go.Bar(
    x = city_sales.loc[cat, 'City'], 
    y = city_sales.loc[cat, dropdown_type],
    marker_color = colors_palette[cat],
    name = cat,
    text=[cat] * len(cities),
    customdata=city_sales.loc[cat,'percents'],
    hovertemplate ='%{text}, '+
                      '%{y:.3s} $<br>'+
                      '%{customdata}% des ventes<br><extra></extra>')
    for cat in categories])

# updates
fig.update_layout(hovermode = 'x unified', barmode='stack',
                  title = 'Volume des ventes par ville et par catégories',
                  xaxis={'categoryorder':'category ascending'},
                  hoverlabel=dict(bgcolor="white",font_size=12),
                  legend=dict(
                      orientation="h",
                      yanchor="bottom", y=1,
                      xanchor="right", x=0.63))

if dropdown_type == 'Sales':
    fig.update_layout(title='Volume des ventes par ville et par catégories') 
    fig.update_yaxes(title='Ventes en $')
else:
    fig.update_layout(title='Volume des commandes par ville et par catégories')
    fig.update_yaxes(title='Nombre de ventes')
    

fig.update_xaxes(showgrid=False)

💬 dans le hover donner le pourcentage de chaque categories

In [385]:
fig = px.pie(data, values='Sales', names='City', color_discrete_sequence=px.colors.sequential.ice)
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.show()

💬 Trouver une palette de couleur sympa pour les villes, à presenter sur la map du début aussi..
https://coolors.co/palettes/trending <br>
💬 travailler le hover

### Map
🤔 pertinance de ce graph?

In [386]:
city_sales = data.groupby(['City','lat','long']).sum()['Sales'].reset_index()
city_sales['Sales_text'] = city_sales['Sales'].apply(lambda x: millify(x))

map_plot = go.Figure(go.Scattermapbox(
        lat = city_sales['lat'], 
        lon = city_sales['long'],
        marker = dict(size=city_sales['Sales'], sizeref = 150000),
        hovertemplate ='<b>%{text}</b><br>' +
                '%{customdata} $<extra></extra>',
        text = city_sales['City'],
        customdata = city_sales['Sales_text']))
                     
map_plot.update_layout(hoverlabel=dict(bgcolor="white",font_size=12),
                       title='Total des ventes durant l’année par ville',
                       width=800, 
                       height=600,
                       mapbox = dict(accesstoken = mapbox_access_token,
                                     zoom = 2.9,
                                     center = go.layout.mapbox.Center(lat=42,lon=-97),
                                    ), 
                       showlegend=False)

map_plot.show()

## 4. Etude temporelle 
---

### Quel a été le meilleur mois de vente ? 

In [387]:
sale_per_month = data.groupby(['Month_num', 'Month'])['Sales'].sum()
sale_per_month = data.groupby(['Month_num', 'Month','Categories']).sum()[dropdown_type]
sale_per_month = sale_per_month.reset_index().set_index('Categories')

In [388]:
best_sale = go.Figure([go.Bar(
    x = sale_per_month.loc[cat,'Month'], 
    y = sale_per_month.loc[cat,dropdown_type],
    marker_color = colors_palette[cat],
    name = cat)
    for cat in categories])



best_sale.update_layout(hovermode="x unified",barmode='stack',
                        title = "Total des ventes regroupé par mois, séparé par catégories",
                        legend=dict(
                            orientation="h",
                            yanchor="bottom", y=1,
                            xanchor="right", x=0.63))
best_sale.update_yaxes(title= 'Ventes en  USD($)')
best_sale.update_xaxes(showgrid=False)
best_sale.show()

💬 travailler le tooltip

↳ les ventes du mois de décembre sont le meilleurs avec des ventes à 4.61 M de dollars il surpasse de 15% le 2eme mois le plus prolifique, Octobre. Quant au mois le moins rentable il s'agit du mois de Janvier avec 1.8 M$ de ventes soit 2XX % moins que le mois de decembre 

### À quelle heure devrions-nous afficher la publicité ? 
pour maximiser la probabilité que le client achète le produit 

In [512]:
filter_city = 'San Francisco'
filter_city = None

In [513]:
if filter_city:
    df = data[data['City'] == filter_city]
else:
    df = data
    
buying_hours = df.groupby('Hour').sum()['Quantity Ordered']

In [514]:
fig = go.Figure(go.Bar(
    x = buying_hours.index,
    y = buying_hours,
    hovertemplate ='<b>%{x}h</b><br>'+
    '%{y:.0f} commandes<extra></extra>'))

fig.update_layout(showlegend=False,
                                hoverlabel=dict(bgcolor="white",font_size=14),
                                title="Nombre de commande par heure durant l’année 2019")
fig.update_yaxes(title= 'Nombre de commande')
fig.update_xaxes(title= "Heure d'achats", showticklabels=False, showgrid=False, zeroline=False)
fig.show()

💬 Laisser à l’utilisateur le libre choix d'explorer lui même ce graph en function de la ville

### Quel est le nombre de produit different acheté par commande?

In [25]:
prod_by_order = data.groupby(['Order ID', 'Order Date']).count()['Product'].value_counts()

In [342]:
# plot
fig = go.Figure(go.Bar(
    x = prod_by_order,
    y = prod_by_order.index,
    orientation='h'))

# updates
fig.update_layout(hoverlabel=dict(bgcolor="white",font_size=14), hovermode='y unified',
                  title = "Nombre de produits achetés par commande")
fig.update_yaxes(title= 'Nombre de produit', showgrid=False)
fig.update_xaxes(showticklabels=False, showgrid=False)
fig.show()

In [79]:
prod_by_order

1    171301
2      6778
3       340
4        17
5         1
Name: Product, dtype: int64

↳ Il y a peu d'achat groupé. 96% des clients n’achète qu'un seul produit. Ce qui peut être amélioré en ajoutant un systeme de promotions sur le deuxième article. 

💬 changer le sens du bar chart<br>
💬 ajouter le % dans le hover

### Quels sont les produits qui sont le plus souvent vendus ensemble ?

In [28]:
# drop the command of only one product
multi_purchase = data[data['Order ID'].duplicated(keep=False)]

In [29]:
# gather in one cell all article purchase by 'Order ID'
multi_purchase.loc[:,'Grouped'] = multi_purchase.groupby('Order ID')['Product'].transform(lambda x: ','.join(x))

/Users/axel/Agensit/venv/lib/python3.8/site-packages/pandas/core/indexing.py:845: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

/Users/axel/Agensit/venv/lib/python3.8/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [30]:
# drop the duplicate ID
multi_purchase = multi_purchase.drop_duplicates(subset='Order ID')

In [31]:
# Count the number of combination 
from itertools import combinations
from collections import Counter

count = Counter()

for row in multi_purchase['Grouped']:
    row_list = row.split(',')
    count.update(Counter(combinations(row_list, 2)))

group_product = {'Product':[], 'Sales':[]}
for key,value in count.most_common(10):
    group_product['Product'].append(key)
    group_product['Sales'].append(value)
    
top_group_sales = pd.DataFrame(group_product)
top_group_sales['Product'] = top_group_sales['Product'].apply(lambda x: f'{x[0]} et {x[1]}')
# top_group_sales.set_index('Product').iplot('bar')

 ↳ Referenced: [stackoverflow](https://stackoverflow.com/questions/52195887/counting-unique-pairs-of-numbers-into-a-python-dictionary)

In [32]:
top_group_sales = top_group_sales.sort_values(by='Sales')
group_sale_plot = go.Figure(go.Bar(y = top_group_sales['Product'],
                                   x = top_group_sales['Sales'],
                                   orientation='h',
                                   hovertemplate ='<b>%{y}</b><br> %{x} commandes<extra></extra>'
                                    ))

group_sale_plot.update_layout(showlegend=False, 
                                hoverlabel=dict(bgcolor="white",font_size=14),
                                title = "Top 10 des produits les plus vendus ensembles")
group_sale_plot.update_yaxes(title= 'Produit', showticklabels=False, showgrid=False)
group_sale_plot.update_xaxes(title= 'Nombre de ventes')
group_sale_plot.show()

### Est ce que le client est satisfait de son achat ?

In [33]:
data.groupby(['Order ID', 'Order Date']).sum().reset_index()['Order ID'].duplicated().value_counts()

False    178437
Name: Order ID, dtype: int64

Aucun client n'est revenu sur le site pour effectuer un deuxième achat..  On remarque ici la limite de nos données qui ont été générées à la main et qui ne sont pas de vrai données .. __On cachera cette partie dans le rapport__ mais on pourra dire qu'il ne s'agit que d'un exemple et que l'on aurait pu réaliser d'autre études. Exemple avec le taux de satisfaction des clients en mesurant le taux de retour sur le site 

# Conclusion

---

Attaquer les problèmes en s’appuyant sur l'analyse des données vous offrent une structure et des principes afin de créer un système précis et pertinant pour systématiquement analyser vos problèmes. Cette extraction de connaissances utile facilite la prises de décisions et vous offrent des avantages décisionnels sur vos concurrents.  Parler du data mining et l'introduire pour un futur projet